In [24]:
import networkx as nx
import networkx as nx
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
from networkx.algorithms import bipartite
import scipy.sparse as sparse
import freeman as fm
from itertools import combinations
import statistics



In [25]:
fm.affiliation_tracking

<function freeman.affiliation_tracking(graphs, nodes, weight='weight', subjects=[])>

In [26]:
df = pd.read_json(r"test.json")
df = df[(df.box_office != "N/A") & (df.genre != 'Adult')& (df.actors != "N/A")].dropna(subset=['box_office'])
df = df[df.genre != "N/A"].dropna(subset=['genre'])
df["box_office"] = df["box_office"].replace(',', '', regex=True).str[1:].astype({"box_office": float})
df = df.sort_values(by=['box_office'], ascending = False)
df = df[df.year != "N/A"].astype({"year": int})
dfcomedy = df

for count, i in zip(df.index, df['genre']):
    if "Comedy" not in i:
        dfcomedy = dfcomedy.drop(count)

dic = {}
listagene = []

def dicionario_atorgenero(df):
    dic = {}
    listagene = []
    for i, j in zip(df["actors"], df["genre"]):
        listator = i.split(', ')
        listagen = j.split(', ')
        for a in listator:
            if a not in dic:
                dic[a] = {}
            for g in listagen:
                if g not in dic[a]:
                    dic[a][g] = 1
                else:
                    dic[a][g] += 1
                if g not in listagene:
                    listagene.append(g)
    try:
        del dic['Fantasy']
    except:
        pass
        
    return dic, listagene

def dicionario_filmesatorep(df):
    dic = {}
   
    for i in df["actors"]:
        listator = i.split(', ')
        perm = combinations(listator, 2)
        for j in list(perm):
            if j not in dic:
                dic[j] = 1
            else:
                dic[j] += 1
    return dic
        
        
listagene = dicionario_atorgenero(df)[1]
dic = dicionario_atorgenero(df)[0]   



In [27]:
#for count, i in zip(df.index, df['genre']):
#    print(df.ix[count])
(df.iloc[4])

title                        Harry Potter and the Sorcerer's Stone
year                                                          2001
rated                                                           PG
released                                               16 Nov 2001
runtime                                                    152 min
genre                                   Adventure, Family, Fantasy
director                                            Chris Columbus
writer             J.K. Rowling (novel), Steve Kloves (screenplay)
actors           Richard Harris, Maggie Smith, Robbie Coltrane,...
plot             An orphaned boy enrolls in a school of wizardr...
language                                                   English
country                                                    UK, USA
awards           Nominated for 3 Oscars. Another 17 wins & 62 n...
poster           https://m.media-amazon.com/images/M/MV5BNjQ3NW...
ratings          [{'source': 'Internet Movie Database', 'value

In [28]:
if 'Avatar' in df['title'].unique():
    print('s')

In [29]:
def graph_onemode(df):
    
    Actor_names = []
    a = dicionario_filmesatorep(df)
    b = dicionario_filmesatorep(df)
    for h in a:
        
        if a[h] <= 1:
            del b[h]
        else:
            if(h[0] not in Actor_names):
                Actor_names.append(h[0])
            if(h[1] not in Actor_names):
                Actor_names.append(h[1])

    B = fm.Graph(nx.empty_graph())

    B.add_nodes_from(Actor_names)
    B.set_all_nodes('size', 1)
    B.set_all_nodes('labpos', 'hover')
    B.label_nodes()
    
    for h in b:
        B.add_edge(h[0],h[1])
    num_edges = B.number_of_edges()
    num_nodes = B.number_of_nodes()
    B.set_all_nodes('labpos','hover')
    return B

## Função que realiza a análise de correspondência

In [30]:
Actor_names = []
allActors = []
for k in dic:
    allActors.append(k) ##Lista que armazena todos os atores
   
allGenres = listagene
# for k in dic:
#     allGenres.append(k) ##Lista que armazena todos os atores
def graph(dic, listagene):
    
    Actor_names = []

    for k in dic:
        Actor_names.append(k)


    B = fm.Graph(nx.empty_graph())
#     B.add_nodes_from(Actor_names,bipartite = 0)
    B.add_nodes_from(allActors,bipartite = 0)
    B.add_nodes_from(allGenres,bipartite = 1)
    B.set_all_nodes('size', 1)
    B.set_all_nodes('labpos', 'hover')
    B.label_nodes()

    for name in Actor_names:
        max_pes = 0
        for j in dic[name]:
            max_pes += dic[name][j] 
        
        for gen in dic[name]:
            B.add_edge(name,gen,color=(0,255,0),weight=dic[name][gen]/max_pes)
            
    num_edges = B.number_of_edges()
    num_nodes = B.number_of_nodes()

    ## Referencia do codigo abaixo do exercicio 3 das aulas. Por algum motivo o bipartite nao funcionou
    B.move('bipartite', [n for n in B.nodes if B.nodes[n]['bipartite'] == 0])
    return B
        

In [31]:
B = graph_onemode(dfcomedy)
B.move('kamada_kawai')
B.draw()

## Two mode Ator-Gênero

In [32]:
graph(dic,listagene).draw()

In [33]:
#TESTA SE TEM ATOR COM NOME DE GENERO
#a = graph(dic, listagene).edges()
#for i in a:
#    if i[0] in listagene:
#        print(i)

dic['Adam Sandler']

{'Comedy': 3,
 'Fantasy': 1,
 'Animation': 1,
 'Musical': 1,
 'Drama': 1,
 'Romance': 1,
 'Thriller': 1}

## Análise de correspondencia( 2000-2010)

In [34]:
B1 = graph(dic, listagene)
B1.label_nodes()
B1.analyze_to_move([n for n in B1.nodes if B1.nodes[n]['bipartite'] == 0])
B1.graph['awidth'] = 1
B1.skin_seaborn([n for n in B1.nodes if B1.nodes[n]['bipartite'] == 0])
B1.set_all_edges('color', (0, 0, 0, 0.0))
B1.graph['width'] = 800
B1.nodes['Comedy']['color'] = (0, 255, 0)
B1.nodes['Comedy']['size'] = 20
B1.nodes['Adam Sandler']['color'] = (0, 255, 0)
B1.nodes['Adam Sandler']['size'] = 20
B1.set_all_nodes('size', 15, filter=lambda n: B1.nodes[n]['bipartite'] == 0)
B1.draw()

## Análise de correspondencia( 2000)

In [15]:
B = graph(dicionario_atorgenero(df[df.year == 2000])[0], dicionario_atorgenero(df[df.year == 2000])[1])

B1 = B
B1.label_nodes()
B1.analyze_to_move([n for n in B1.nodes if B1.nodes[n]['bipartite'] == 0])
B1.graph['awidth'] = 1
B1.skin_seaborn([n for n in B1.nodes if B1.nodes[n]['bipartite'] == 0])
B1.set_all_edges('color', (0, 0, 0, 0.0))
B1.graph['width'] = 800
B1.nodes['Comedy']['color'] = (0, 255, 0)
B1.nodes['Comedy']['size'] = 20
B1.set_all_nodes('size', 15, filter=lambda n: B1.nodes[n]['bipartite'] == 0)
B1.draw()

## Análise de correspondencia(2001)

In [16]:
B = graph(dicionario_atorgenero(df[df.year == 2001])[0], dicionario_atorgenero(df[df.year == 2001])[1])

B1 = B
B1.label_nodes()
B1.analyze_to_move([n for n in B1.nodes if B1.nodes[n]['bipartite'] == 0])
B1.graph['awidth'] = 1
B1.skin_seaborn([n for n in B1.nodes if B1.nodes[n]['bipartite'] == 0])
B1.set_all_edges('color', (0, 0, 0, 0.0))
B1.graph['width'] = 800
B1.nodes['Comedy']['color'] = (0, 255, 0)
B1.nodes['Comedy']['size'] = 20
B1.set_all_nodes('size', 15, filter=lambda n: B1.nodes[n]['bipartite'] == 0)
B1.draw()

In [17]:
G1 = graph_onemode(dicionario_atorgenero(df[df.year == '2001'])[0], dicionario_atorgenero(df[df.year == '2001']))
G1.move('kamada_kawai')
G1.draw()

/usr/local/lib/python3.7/site-packages/pandas/core/ops/__init__.py:1115: FutureWarning:

elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison



TypeError: graph_onemode() takes 1 positional argument but 2 were given

In [18]:
B = graph(dicionario_atorgenero(df[df.year == 2002])[0], dicionario_atorgenero(df[df.year == 2002])[1])

B1 = B
B1.label_nodes()
B1.analyze_to_move([n for n in B1.nodes if B1.nodes[n]['bipartite'] == 0])
B1.graph['awidth'] = 1
B1.skin_seaborn([n for n in B1.nodes if B1.nodes[n]['bipartite'] == 0])
B1.set_all_edges('color', (0, 0, 0, 0.0))
B1.graph['width'] = 800
B1.nodes['Comedy']['color'] = (0, 255, 0)
B1.nodes['Comedy']['size'] = 20
B1.set_all_nodes('size', 15, filter=lambda n: B1.nodes[n]['bipartite'] == 0)
B1.draw()

## Análise de correspondencia(2003)

In [19]:
B = graph(dicionario_atorgenero(df[df.year == 2003])[0], dicionario_atorgenero(df[df.year == 2003])[1])

B1 = B
B1.label_nodes()
B1.analyze_to_move([n for n in B1.nodes if B1.nodes[n]['bipartite'] == 0])
B1.graph['awidth'] = 1
B1.skin_seaborn([n for n in B1.nodes if B1.nodes[n]['bipartite'] == 0])
B1.set_all_edges('color', (0, 0, 0, 0.0))
B1.graph['width'] = 800
B1.nodes['Comedy']['color'] = (0, 255, 0)
B1.nodes['Comedy']['size'] = 20
B1.set_all_nodes('size', 15, filter=lambda n: B1.nodes[n]['bipartite'] == 0)
B1.draw()

## Análise de correspondencia(2004)

In [20]:
B = graph(dicionario_atorgenero(df[df.year == 2004])[0], dicionario_atorgenero(df[df.year == 2004])[1])

B1 = B
B1.label_nodes()
B1.analyze_to_move([n for n in B1.nodes if B1.nodes[n]['bipartite'] == 0])
B1.graph['awidth'] = 1
B1.skin_seaborn([n for n in B1.nodes if B1.nodes[n]['bipartite'] == 0])
B1.set_all_edges('color', (0, 0, 0, 0.0))
B1.graph['width'] = 800
B1.nodes['Comedy']['color'] = (0, 255, 0)
B1.nodes['Comedy']['size'] = 20
B1.set_all_nodes('size', 15, filter=lambda n: B1.nodes[n]['bipartite'] == 0)
B1.draw()

In [21]:
# G1 = graph_onemode(df[df.year < 2004])
# G1.move('kamada_kawai')
# G1.draw()

# G1 = graph_onemode(df[df.year < 2005])
# G1.move('kamada_kawai')
# G1.draw()

# G1 = graph_onemode(df[df.year < 2006])
# G1.move('kamada_kawai')
# G1.draw()

# G1 = graph_onemode(df[df.year < 2007])
# G1.move('kamada_kawai')
# G1.draw()

# G1 = graph_onemode(df[df.year < 2008])
# G1.move('kamada_kawai')
# G1.draw()

# G1 = graph_onemode(df[df.year < 2009])
# G1.move('kamada_kawai')
# G1.draw()

# G1 = graph_onemode(df[df.year < 2010])
# G1.move('kamada_kawai')
# G1.draw()


In [22]:
listagrafo = []
b = 2000

for i in range(9):
    listagrafo.append(graph(dicionario_atorgenero(df[df.year == b])[0], dicionario_atorgenero(df[df.year == b])[1]))
    b += 1
    

In [23]:
B = fm.affiliation_animation(listagrafo,allActors)
for n in B.nodes:
   if B.nodes[n]['id'] != 'Comedy' and B.nodes[n]['id'] != 'Adam Sandler':
       B.nodes[n]['size'] = 1
# B.play()

AttributeError: 'Animation' object has no attribute 'nodes'

In [ ]:
l = listagrafo[-1]
fm.analyze_last_to_move_all(listagrafo, [n for n in l.nodes if l.nodes[n]['bipartite'] == 0])

In [ ]:
s = fm.Graph(fm.stack_and_track(listagrafo))

In [ ]:
s.set_all_nodes('size', 5)
s.draw()